In [1]:
import os
os.environ['KMP_DUPLICATE_LIB_OK']='True'

# Verify GPU availability
import torch
print("CUDA available:", torch.cuda.is_available())
print("GPU device name:", torch.cuda.get_device_name(0) if torch.cuda.is_available() else "No GPU")
print("PyTorch version:", torch.__version__)
print("CUDA version:", torch.version.cuda if torch.cuda.is_available() else "Not available")

CUDA available: True
GPU device name: NVIDIA GeForce RTX 3050 Laptop GPU
PyTorch version: 2.5.1
CUDA version: 11.8


In [2]:
from pathlib import Path
import torch
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import importlib

import poseidonPcModules as ppm
import gradNorm as gn
import poseidonModelWrapper as pmw
import poseidonTrainer as pt
from poseidonDataLoader import poseidonDataLoaderMri

data_root = Path("MARS_SRCmpmri_MAXPPL4_GRID8_NORMED") / "src"
tr_root = data_root / "train"
ts_root = data_root / "test"

TRAINING_PARAMETERS = {'num_epochs': 100,
                       'kpt_loss_weight': 0.01,
                       'presence_loss_weight': 2,
                       'contrastive_loss_weight': 0.5,
                       'batch_size': 100}
5
#mpMRI specific parameters
NUM_KPTS = 17 #mRI poses follow the 17-keypoint COCO structure
PC_GRID_DIM = 16
MAX_POSES = 4

splits = ["train", "test"]
drs = {}
pdls = {}
dls = {}

#get the PyTorch dataloader for the multi-person mRI dataset (mpmRI)
for sp in splits:
    drs[sp] = data_root / sp
    pdls[sp] = poseidonDataLoaderMri(drs[sp], batch_size=TRAINING_PARAMETERS['batch_size'], shuffle=True)
    dls[sp] = pdls[sp].get_dataloader()


c:\Users\aarub\POST\thesis_project-main\prior_filter.py:15: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  prior.load_state_dict(torch.load(PRIOR_PATH, map_location='cpu')['m

In [3]:
import poseidonPcModules as ppm
import gradNorm as gn
import poseidonModelWrapper as pmw
from poseidonTrainer import poseidonPoseTrainer

def build_mhpe_wrapper():
    #build wrapper for mpMARS using mpmRI dataset
    pc_encoder = ppm.poseidonPcEncoder(grid_dims=(PC_GRID_DIM,PC_GRID_DIM))
    pose_estimator = ppm.poseidonPoseEstimator(max_poses=MAX_POSES,num_kpts=NUM_KPTS)
    #grad_norm = gn.gradNorm(layer=pc_encoder.encoder.embedding_layer, lr=5e-4, alpha=0.12)
   # model_wrapper = pmw.poseidonModelWrapper(pc_encoder=pc_encoder, pose_estimator=pose_estimator, grad_norm=grad_norm)
    model_wrapper = pmw.poseidonModelWrapper(pc_encoder=pc_encoder, pose_estimator=pose_estimator)
    
    return model_wrapper

model_wrapper = build_mhpe_wrapper()

In [4]:
ptfw = poseidonPoseTrainer(model_wrapper, TRAINING_PARAMETERS)

Using device: cuda
pc_encoder params: {'learning_rate': 0.0001, 'weight_decay': 0.0001, 'scheduler_step_size': 3, 'scheduler_gamma': 0.95}
pose_estimator params: {'learning_rate': 0.0001, 'weight_decay': 0.0001, 'scheduler_step_size': 3, 'scheduler_gamma': 0.95}


In [5]:
ptfw.train(dls['train'], dls['test'])
#pred_pose: bs,(max_ppl+1)+max_ppl*num_kpts*kpt_dims

Starting epoch 1/100
Initial GPU Memory allocated: 17.97 MB
Initial GPU Memory cached: 18.00 MB
Train Batch [0/1639] - Batch Loss: 0.5430, Running Mean: 0.2730, Running Std: 0.0000
Train Batch [5/1639] - Batch Loss: 0.5491, Running Mean: 0.2821, Running Std: 0.0104
Train Batch [10/1639] - Batch Loss: 0.5508, Running Mean: 0.2881, Running Std: 0.0107
Train Batch [15/1639] - Batch Loss: 0.5515, Running Mean: 0.2904, Running Std: 0.0108
Train Batch [20/1639] - Batch Loss: 0.5361, Running Mean: 0.2900, Running Std: 0.0106
Train Batch [25/1639] - Batch Loss: 0.5047, Running Mean: 0.2899, Running Std: 0.0096
Train Batch [30/1639] - Batch Loss: 0.5216, Running Mean: 0.2909, Running Std: 0.0091
Train Batch [35/1639] - Batch Loss: 0.5303, Running Mean: 0.2910, Running Std: 0.0093
Train Batch [40/1639] - Batch Loss: 0.5273, Running Mean: 0.2916, Running Std: 0.0094
Train Batch [45/1639] - Batch Loss: 0.5301, Running Mean: 0.2916, Running Std: 0.0105
Train Batch [50/1639] - Batch Loss: 0.5123, Ru

c:\Users\aarub\POST\thesis_project-main\poseidonTrainer.py:86: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  self.train_df = pd.concat([self.train_df, eptr_results], ignore_index=True)
c:\Users\aarub\POST\thesis_project-main\poseidonTrainer.py:88: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  self.val_df = pd.concat([self.val_df, epvl_results], ignore_index=True)


Model checkpoint saved to results\last_model.pth
Model checkpoint saved to results\best_model.pth
Starting epoch 2/100
Initial GPU Memory allocated: 88.10 MB
Initial GPU Memory cached: 102.00 MB
Train Batch [0/1639] - Batch Loss: 0.3394, Running Mean: 0.2732, Running Std: 0.0000
Train Batch [5/1639] - Batch Loss: 0.3476, Running Mean: 0.2743, Running Std: 0.0119
Train Batch [10/1639] - Batch Loss: 0.3652, Running Mean: 0.2805, Running Std: 0.0125
Train Batch [15/1639] - Batch Loss: 0.3703, Running Mean: 0.2808, Running Std: 0.0113
Train Batch [20/1639] - Batch Loss: 0.3941, Running Mean: 0.2833, Running Std: 0.0112
Train Batch [25/1639] - Batch Loss: 0.3572, Running Mean: 0.2836, Running Std: 0.0105
Train Batch [30/1639] - Batch Loss: 0.3708, Running Mean: 0.2831, Running Std: 0.0098
Train Batch [35/1639] - Batch Loss: 0.3632, Running Mean: 0.2834, Running Std: 0.0095
Current loss: 0.3071
Mean loss: 0.2838
Std loss: 0.0099
Train Batch [40/1639] - Batch Loss: 0.3681, Running Mean: 0.283

: 